# Example

In [9]:
import plotly.express as px
df = px.data.gapminder()
px.scatter(df, x="gdpPercap", y="lifeExp", animation_frame="year", animation_group="country",
           size="pop", color="continent", hover_name="country",
           log_x=True, size_max=55, range_x=[100,100000], range_y=[25,90])

In [10]:
# fig = px.scatter(df, x="gdpPercap", y="lifeExp", animation_frame="year", animation_group="country",
#            size="pop", color="continent", hover_name="country",
#            log_x=True, size_max=55, range_x=[100,100000], range_y=[25,90])


# import dash
# import dash_core_components as dcc
# import dash_html_components as html

# external_stylesheets = ['https://codepen.io/chriddyp/pen/bWLwgP.css']

# app = dash.Dash()
# app.layout = html.Div([
#     html.H1(children='Test Dash'),
#     html.Div(children="La visualisation est assez réactive sans trop de latences?"),   
#     dcc.Graph(figure=fig)
# ])

# app.run_server(debug=True, use_reloader=False)  # Turn off reloader if inside Jupyter

# Create a map

In [187]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

In [265]:
df = pd.read_csv("database.csv")
df.head()

Province/State Country/Region   Lat  Long        Date  Confirmed  Death  \
0    Afghanistan    Afghanistan  33.0  65.0  2020-01-22          0      0   
1    Afghanistan    Afghanistan  33.0  65.0  2020-01-23          0      0   
2    Afghanistan    Afghanistan  33.0  65.0  2020-01-24          0      0   
3    Afghanistan    Afghanistan  33.0  65.0  2020-01-25          0      0   
4    Afghanistan    Afghanistan  33.0  65.0  2020-01-26          0      0   

   Recovered  
0        0.0  
1        0.0  
2        0.0  
3        0.0  
4        0.0

In [230]:
# df1 = df[df["Date"]=="2020-05-23"]
df["color"]= df["Confirmed"].map(lambda x: np.log2(x+1e-6))

mapbox_access_token = "pk.eyJ1IjoiYXhlbGl0b3Jvc2FsaXRvIiwiYSI6ImNrYjJmMTZuOTBheHEyc243Mjl5ZXNuMTMifQ.Yp-TD_DLMvwB4UYP_xYehA"

px.set_mapbox_access_token(mapbox_access_token)
fig = px.scatter_mapbox(df, lat="Lat", lon="Long", 
                        hover_name="Country/Region",
                        zoom=0.6, mapbox_style='dark',
                        size="Confirmed", size_max=50,
                        animation_frame="Date",
                        color="color", color_continuous_scale="ylorrd",)


fig.update(layout_coloraxis_showscale=False)

fig.show()

### Downsampling

In [272]:
df = pd.read_csv("database.csv")
down_df = df.copy()

In [273]:
down_df["Date"] = pd.to_datetime(down_df["Date"])
down_df = down_df.set_index("Date").groupby("Province/State").resample('15D', kind="period").sum()
down_df.reset_index(inplace=True)
down_df.drop(columns=["Lat","Long"], inplace=True)
down_df

Province/State       Date  Confirmed  Death  Recovered
0       Afghanistan 2020-01-22          0      0        0.0
1       Afghanistan 2020-02-06          0      0        0.0
2       Afghanistan 2020-02-21         12      0        0.0
3       Afghanistan 2020-03-07        197      0        6.0
4       Afghanistan 2020-03-22       2455     59       70.0
...             ...        ...        ...    ...        ...
2380       Zimbabwe 2020-03-22         93     14        0.0
2381       Zimbabwe 2020-04-06        263     42       10.0
2382       Zimbabwe 2020-04-21        487     59       57.0
2383       Zimbabwe 2020-05-06        587     60      177.0
2384       Zimbabwe 2020-05-21        270     20      104.0

[2385 rows x 5 columns]

↳ Latitude and Longtitude are lost with the `.sum()`

In [274]:
df.iloc[:,:4]

Province/State Country/Region        Lat       Long
0        Afghanistan    Afghanistan  33.000000  65.000000
1        Afghanistan    Afghanistan  33.000000  65.000000
2        Afghanistan    Afghanistan  33.000000  65.000000
3        Afghanistan    Afghanistan  33.000000  65.000000
4        Afghanistan    Afghanistan  33.000000  65.000000
...              ...            ...        ...        ...
33245        Lesotho        Lesotho -29.609988  28.233608
33246        Lesotho        Lesotho -29.609988  28.233608
33247        Lesotho        Lesotho -29.609988  28.233608
33248        Lesotho        Lesotho -29.609988  28.233608
33249        Lesotho        Lesotho -29.609988  28.233608

[33250 rows x 4 columns]

In [275]:
test = pd.merge(down_df,df.iloc[:,:4])

In [281]:
test.drop_duplicates(inplace=True)
test.reset_index(inplace=True)

In [282]:
test["Date"] = test["Date"].astype(str)

In [283]:
test["color"]= test["Confirmed"].map(lambda x: np.log2(x+1e-6))
px.set_mapbox_access_token(mapbox_access_token)
fig = px.scatter_mapbox(test, lat="Lat", lon="Long", 
                        hover_name="Country/Region",
                        zoom=0.6, mapbox_style='dark',
                        size="Confirmed", size_max=50,
                        animation_frame="Date",
                        color="color",color_continuous_scale="ylorrd",)


fig.update(layout_coloraxis_showscale=False)

fig.show()

In [284]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2394 entries, 0 to 2393
Data columns (total 10 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   index           2394 non-null   int64  
 1   Province/State  2394 non-null   object 
 2   Date            2394 non-null   object 
 3   Confirmed       2394 non-null   int64  
 4   Death           2394 non-null   int64  
 5   Recovered       2394 non-null   float64
 6   Country/Region  2241 non-null   object 
 7   Lat             2394 non-null   float64
 8   Long            2394 non-null   float64
 9   color           2394 non-null   float64
dtypes: float64(4), int64(3), object(3)
memory usage: 187.2+ KB


In [286]:
test[test.isnull()]

index Province/State Date  Confirmed  Death  Recovered Country/Region  \
0       NaN            NaN  NaN        NaN    NaN        NaN            NaN   
1       NaN            NaN  NaN        NaN    NaN        NaN            NaN   
2       NaN            NaN  NaN        NaN    NaN        NaN            NaN   
3       NaN            NaN  NaN        NaN    NaN        NaN            NaN   
4       NaN            NaN  NaN        NaN    NaN        NaN            NaN   
...     ...            ...  ...        ...    ...        ...            ...   
2389    NaN            NaN  NaN        NaN    NaN        NaN            NaN   
2390    NaN            NaN  NaN        NaN    NaN        NaN            NaN   
2391    NaN            NaN  NaN        NaN    NaN        NaN            NaN   
2392    NaN            NaN  NaN        NaN    NaN        NaN            NaN   
2393    NaN            NaN  NaN        NaN    NaN        NaN            NaN   

      Lat  Long  color  
0     NaN   NaN    NaN  
1     NaN   NaN    NaN  
2     NaN   NaN    NaN  
3     NaN   NaN    NaN  
4     NaN   NaN    NaN  
...   ...   ...    ...  
2389  NaN   NaN    NaN  
2390  NaN   NaN    NaN  
2391  NaN   NaN    NaN  
2392  NaN   NaN    NaN  
2393  NaN   NaN    NaN  

[2394 rows x 10 columns]

## TODO
- mettre au propre
- Grouper par bucket de 15 jours (create a TimeSerie column Periode of 15 days then `groupby().max`)
- ajouter une bordure blanche aux bulles
- Changer la forme des tooltips